In [184]:
import tensorflow as tf
import numpy as np
# import librosa
# import librosa.display
import matplotlib.pyplot as plt

filename = 'filtered_data_keyboard.tfrecord'
dataset = tf.data.TFRecordDataset(filename)

In [185]:
epoch = 10
dataset = dataset.repeat(epoch)
iterator = dataset.make_one_shot_iterator()
next_element = iterator.get_next()
sess = tf.Session()

num_batch = 0
j = 0
audio_arr = []
instrumentFamily_arr = []
while True:
    value = sess.run(next_element)
    example = tf.train.Example()
    example.ParseFromString(value)
    f = example.features.feature
    audio = np.array(f['audio'].float_list.value[:784])
    audio_arr.append(audio)
    instrumentFamily = np.int32(f['instrument_family'].int64_list.value[0])
    instrumentFamily_arr.append(instrumentFamily)
    j += 1
    if j>100:
        break
print("Done")
audio_arr = np.asarray(audio_arr)
instrumentFamily_arr = np.asarray(instrumentFamily_arr)

Done


In [186]:
def cnn_model_fn(features, labels, mode):
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])
    
    # Input Tensor Shape: [batch_size, 28, 28, 1]
    # Output Tensor Shape: [batch_size, 28, 28, 32]
    conv1 = tf.layers.conv2d(
        inputs=input_layer,
        filters=32,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu
    )
    
    print(conv1)

    # Input Tensor Shape: [batch_size, 28, 28, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 32]
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)
    
    print(pool1)
    
    # Input Tensor Shape: [batch_size, 14, 14, 32]
    # Output Tensor Shape: [batch_size, 14, 14, 64]
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu
    )
    
    print(conv2)

    # Input Tensor Shape: [batch_size, 14, 14, 64]
    # Output Tensor Shape: [batch_size, 7, 7, 64]
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)
    
    print(pool2)
    
    # Input Tensor Shape: [batch_size, 7, 7, 64]
    # Output Tensor Shape: [batch_size, 7 * 7 * 64]
    pool2_flat = tf.reshape(pool2, [-1, 7*7*64])
    
    print(pool2_flat)
    
    # Input Tensor Shape: [batch_size, 7 * 7 * 64]
    # Output Tensor Shape: [batch_size, 1024]
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    
    print(dense)
    
    # Add dropout operation; 0.6 probability that element will be kept
    dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)
    
    # Input Tensor Shape: [batch_size, 1024]
    # Output Tensor Shape: [batch_size, 10]
    logits = tf.layers.dense(inputs=dropout, units=10)
    print(logits)
    print(labels)
    predictions = {
        "classes": tf.argmax(input=logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)
    
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
          loss=loss,
          global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)
    
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
            labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
        mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [187]:
def main(unused_argv):
    # Load training and eval data
#     mnist = tf.contrib.learn.datasets.load_dataset("mnist")
#     train_data = mnist.train.images # Returns np.array
    train_data = audio_arr
    print(type(train_data))
    print(type(train_data[0]))
#     train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    train_labels = instrumentFamily_arr
    print(train_labels)
#     eval_data = mnist.test.images # Returns np.array
#     eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    mnist_classifier = tf.estimator.Estimator(
        model_fn=cnn_model_fn)
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)
#     # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": train_data},
        y=train_labels,
        batch_size=100,
        num_epochs=None,
        shuffle=True)
    print(train_input_fn)
    mnist_classifier.train(
        input_fn=train_input_fn,
        steps=20000,
        hooks=[logging_hook])
#     eval_input_fn = tf.estimator.inputs.numpy_input_fn(
#       x={"x": eval_data},
#       y=eval_labels,
#       num_epochs=1,
#       shuffle=False)
#     eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
#     print(eval_results)

In [188]:
if __name__ == "__main__":
    tf.app.run()

<class 'numpy.ndarray'>
<class 'numpy.ndarray'>
[4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4
 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4
 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4 4]
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': 'C:\\Users\\Brian\\AppData\\Local\\Temp\\tmpjqstzs8x', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x00000298716FBC18>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
<function numpy_input_fn.<locals>.input_fn at 0

INFO:tensorflow:loss = 2.2772347927093506, step = 0
INFO:tensorflow:probabilities = [[0.08176287 0.09507839 0.08911986 0.08548512 0.17263981 0.0890699
  0.0901167  0.10097304 0.09060661 0.10514772]
 [0.09257962 0.09790981 0.09123105 0.08727892 0.1538852  0.09674697
  0.0844888  0.10030194 0.10031999 0.0952577 ]
 [0.09312294 0.10612243 0.07988409 0.07817806 0.19100644 0.0866943
  0.08103942 0.09800205 0.09548109 0.09046917]
 [0.0886857  0.10683842 0.09704245 0.08755695 0.16233851 0.09557224
  0.08288711 0.09372357 0.09206059 0.09329445]
 [0.07973865 0.09735191 0.09404681 0.07903573 0.20671581 0.0795208
  0.08615639 0.08756629 0.08881173 0.10105588]
 [0.08408328 0.08344926 0.08913616 0.08733745 0.18849742 0.08827363
  0.08939829 0.09167285 0.08903046 0.10912119]
 [0.08208069 0.10432153 0.10056125 0.08708677 0.20578761 0.08053115
  0.07843726 0.08487286 0.08753627 0.08878461]
 [0.09204599 0.09711945 0.09782259 0.0860463  0.15519164 0.09681567
  0.08574541 0.09674307 0.1018305  0.09063936]

INFO:tensorflow:global_step/sec: 11.7773
INFO:tensorflow:probabilities = [[0.0441547  0.07175837 0.05251257 0.05257959 0.53140174 0.04663557
  0.04265753 0.05703817 0.05496483 0.04629693]
 [0.05710976 0.0570592  0.05761003 0.04881949 0.5284807  0.03775979
  0.04243379 0.05608935 0.07041656 0.04422133]
 [0.04890826 0.04547258 0.04887767 0.03320421 0.53844646 0.05185319
  0.05006661 0.05625197 0.0685665  0.05835254]
 [0.06291722 0.08004174 0.07279601 0.05579786 0.4356203  0.05460594
  0.04414252 0.06868029 0.06743425 0.05796386]
 [0.03991718 0.04644747 0.0400209  0.05347347 0.6240359  0.03660301
  0.03531719 0.05107963 0.03850234 0.03460292]
 [0.04725971 0.0446625  0.0427265  0.05054323 0.59265231 0.04297202
  0.03341443 0.05815479 0.04378657 0.04382794]
 [0.07063558 0.06737368 0.06201561 0.05303494 0.44933962 0.06632582
  0.04371469 0.06662504 0.06702375 0.05391128]
 [0.05334454 0.05297713 0.04823191 0.04849595 0.57317886 0.04250512
  0.03473422 0.04598295 0.0470527  0.05349661]
 [0.057

INFO:tensorflow:loss = 0.6443933248519897, step = 100 (8.497 sec)
INFO:tensorflow:probabilities = [[0.01743605 0.01190776 0.01301126 0.00592541 0.89928548 0.01051709
  0.0068881  0.01091174 0.00902341 0.01509369]
 [0.02270575 0.01761347 0.01419587 0.00986097 0.85926545 0.01411257
  0.01252751 0.01897825 0.01858556 0.0121546 ]
 [0.05174253 0.05697321 0.04973624 0.04205755 0.55434742 0.04939756
  0.03647499 0.04254717 0.05490373 0.0618196 ]
 [0.03779256 0.02966227 0.0321692  0.03367628 0.70298965 0.02983866
  0.02582078 0.03423905 0.04037571 0.03343583]
 [0.01109607 0.00975275 0.01068015 0.00817679 0.90414956 0.00822724
  0.00830702 0.01536594 0.01182488 0.0124196 ]
 [0.03283988 0.04054398 0.04221459 0.0320929  0.65518566 0.03813344
  0.03501899 0.03943043 0.04058854 0.04395159]
 [0.01272001 0.02424912 0.01490792 0.01017523 0.87218391 0.00968839
  0.00934748 0.01383985 0.01428345 0.01860463]
 [0.02124719 0.02778548 0.02679423 0.02436255 0.78833228 0.01903072
  0.0189688  0.02285412 0.030

INFO:tensorflow:global_step/sec: 12.0008
INFO:tensorflow:probabilities = [[0.02100823 0.01986512 0.02483979 0.01278288 0.83458017 0.0149382
  0.01611289 0.02060139 0.01932307 0.01594827]
 [0.00809096 0.01225855 0.00594905 0.00428704 0.9371622  0.0057036
  0.0054917  0.00692053 0.00560823 0.00852816]
 [0.00423476 0.00381517 0.00472046 0.00338407 0.96304388 0.00440009
  0.00390601 0.0042877  0.00461083 0.00359705]
 [0.00461673 0.00401558 0.00528853 0.00199125 0.96821279 0.00283226
  0.00163773 0.00313204 0.00409277 0.00418033]
 [0.00473798 0.00909755 0.00582637 0.00417853 0.93911123 0.00664736
  0.00468069 0.01168304 0.00801558 0.00602167]
 [0.0128297  0.01879413 0.01007728 0.01181158 0.87579014 0.01634611
  0.00979348 0.01717621 0.01600894 0.01137242]
 [0.00609894 0.00623936 0.00679931 0.00363002 0.94371147 0.00636297
  0.00441309 0.00794457 0.00857493 0.00622532]
 [0.00514625 0.00844122 0.00860459 0.00585301 0.93628131 0.00602976
  0.00626097 0.00888694 0.00619114 0.00830482]
 [0.00833

...

INFO:tensorflow:global_step/sec: 12.1125
INFO:tensorflow:probabilities = [[0.00000263 0.00000309 0.00000359 0.00000148 0.99996885 0.00000416
  0.00000219 0.00000508 0.00000677 0.00000216]
 [0.00000278 0.00000555 0.00000867 0.0000018  0.99996237 0.00000405
  0.00000164 0.00000458 0.00000664 0.00000192]
 [0.00000294 0.00000848 0.0000039  0.0000023  0.99996668 0.00000273
  0.00000242 0.00000223 0.00000591 0.0000024 ]
 [0.00000006 0.00000007 0.00000005 0.00000003 0.99999943 0.00000005
  0.00000002 0.00000012 0.00000012 0.00000005]
 [0.00002449 0.00001841 0.00001557 0.00001173 0.99983465 0.0000159
  0.00001388 0.00002086 0.00002022 0.0000243 ]
 [0.00000126 0.00000094 0.00000057 0.00000026 0.99999356 0.0000013
  0.0000002  0.00000133 0.00000035 0.00000024]
 [0.00001641 0.00000989 0.00000931 0.00000624 0.99989304 0.0000164
  0.00000526 0.00002163 0.00001313 0.00000869]
 [0.0000013  0.00000197 0.00000468 0.0000013  0.9999824  0.00000101
  0.00000041 0.0000011  0.0000021  0.00000374]
 [0.000000

INFO:tensorflow:loss = 5.827899440191686e-05, step = 19900 (8.255 sec)
INFO:tensorflow:probabilities = [[0.00000121 0.00000126 0.00000136 0.00000031 0.99998979 0.00000054
  0.00000174 0.00000115 0.00000135 0.00000129]
 [0.00015041 0.00004028 0.00010311 0.0000491  0.9992908  0.00008139
  0.0000238  0.00008591 0.00012174 0.00005347]
 [0.00000251 0.00000271 0.00000298 0.00000136 0.99998004 0.00000317
  0.00000166 0.000003   0.00000169 0.00000089]
 [0.00000075 0.00000049 0.00000047 0.00000045 0.99999319 0.00000062
  0.00000025 0.00000188 0.00000095 0.00000096]
 [0.00012352 0.00009185 0.00008996 0.00004669 0.99915986 0.00005825
  0.00005127 0.00011378 0.00011908 0.00014574]
 [0.00004332 0.00005233 0.00004486 0.00001678 0.99965988 0.00002297
  0.0000379  0.00003349 0.00004135 0.00004712]
 [0.00000063 0.00000119 0.00000062 0.00000035 0.99999207 0.0000013
  0.00000041 0.00000179 0.00000065 0.00000099]
 [0.00001804 0.00002368 0.00001923 0.00000996 0.9998386  0.00002042
  0.00001764 0.00002154 0

INFO:tensorflow:Saving checkpoints for 20000 into C:\Users\Brian\AppData\Local\Temp\tmpjqstzs8x\model.ckpt.
INFO:tensorflow:Loss for final step: 6.435999239329249e-05.


SystemExit: 

C:\Users\Brian\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
